The following cell sets the input values required to run the the optimisation model ``..\MINIZINC\hydrogen_plant.mzn``.

This input data are stored in ``..\MINIZINC\hydrogen_plant_data.dzn``. This input file preparation is carried out by ``make_dzn_file`` function that is in ``..\PYTHON\PACKAGE\optimisation.py``.

Then the minizinc optimisation is executed by ``optimise()`` function that is in ``..\PYTHON\PACKAGE\optimisation.py``. 

``projdirs`` stores the key paths for the entire package.

### Set the location and get the solar and wind source data

In [1]:
import pandas as pd
import numpy as np
import os
from projdirs import datadir #load the path that contains the data files 
from PACKAGE.optimisation import make_dzn_file, optimise
from PACKAGE.component_model import WindSource, SolarResource,pv_gen, wind_gen,solcast_weather, SolarResource_solcast, WindSource_solcast

# Set the location

#Newman
Newman = [-23.35, 119.75]
Sydney = [-33.856784, 151.215297]
Tom_Price = [-22.69, 117.79]
Port_Augusta = [-32.49, 137.77]
Whyalla = [-33.04, 137.59]
Pinjarra = [-32.63, 115.87]
Gladstone = [-23.84, 151.25]
Burnie = [-41.05, 145.91]

# Get wind and solar data for the designated location
# WindSource(Lat, Lon)
# SolarResource(Lat,Lon)


# solcast_weather(Newman)
# SolarResource_solcast()
# WindSource_solcast()

### Set the inputs for plant optimisation and run the optimisation

In [16]:
pv_ref_capa = 1e3 #(kW)
pv_ref_out = pv_gen(pv_ref_capa)

wind_ref_capa = 50e3 #(kW)
wind_ref_out = wind_gen()

def AUD2USD(value):
    return(0.746 * value)

# create a dictionary that contains the inputs for optimisation.
#these inputs are used by make_dzn_file function to create an input text file called hydrogen_plant_data.dzn. 
simparams = dict(DT = 1,#[s] time steps
                 ETA_EL = 0.70,       #efficiency of electrolyser
                 BAT_ETA_in = 0.95,   #charging efficiency of battery
                 BAT_ETA_out = 0.95,  #discharg efficiency of battery
                 C_PV = AUD2USD(1258),          #[USD/kW] unit cost of PV
                 C_W = AUD2USD(1934),           #[USD/kW] unit cost of Wind
                 C_EL = 835,          #[USD/W] unit cost of electrolyser
                 C_HS = 95,           #[$/kgH] unit cost of hydrogen storage
                 C_BAT_energy = AUD2USD(400),        #[USD/kWh] unit cost of battery energy storage
                 C_BAT_power = 60,        #[$/kW] unit cost of battery power capacpity
                 CF = 1,           #capacity factor
                 PV_ref_capa = pv_ref_capa,    #capacity of reference PV plant (kW)
                 PV_ref_out = pv_ref_out,           #power output from reference PV plant (kW)
                 Wind_ref_capa = wind_ref_capa,      #capacity of reference wind farm (kW)
                 Wind_ref_out = wind_ref_out,        #power output from the reference wind farm (kW)
                 L = [5 for i in range(len(pv_ref_out))])       #[kgH2/s] load profile timeseries

#run the optimisation function and get the results in a dictionary:
results = optimise(simparams)

# refine the cost of storage
from numpy import log10
def c_hs(hs_max):
    if hs_max>20:
        cost=10 ** (0.212669*(log10(hs_max))**2 - 1.638654*(log10(hs_max)) + 4.403100)
    else:
        cost = 10 ** (-0.0285*log10(hs_max)  + 2.7853)
    return(cost)

while abs(simparams['C_HS'] - c_hs(results['hs_max'][0]/1e3))/simparams['C_HS'] > 0.05:
    print('Hydrogen storage capacity = %0.2f [T of H2]' %( results['hs_max'][0]/1e3 ))
    new_C_HS = c_hs(results['hs_max'][0]/1e3)
    print('new C_HS=', new_C_HS)
    simparams['C_HS'] = new_C_HS
    results = optimise(simparams)
          
          
print (
        'CAPEX = %0.2f [USD]' %( results['CAPEX'][0] ),'\n'
        'PV rated capacity  = %0.2f [kW]' %( results['pv_max'][0] ),'\n'  
        'Wind rated capacity = %0.2f [kW]' %( results['w_max'][0] ),'\n'    
        'Electrolyser rated capacity = %0.4f [kW]' %( results['el_max'][0] ),'\n'  
        'Hydrogen storage capacity = %0.2f [kg of H2]' %( results['hs_max'][0] ),'\n'  
        'Battery energy capacity = %0.2f [kWh]' %( results['bat_capa'][0]  ),'\n'  
        'Battery power capcity = %0.2f [kW]' %( results['bat_pmax'][0] )
        )


Hydrogen storage capacity = 7560.48 [T of H2]
new C_HS= 17.648598068246834
CAPEX = 6363280452.90 [USD] 
PV rated capacity  = 4179531.76 [kW] 
Wind rated capacity = 0.00 [kW] 
Electrolyser rated capacity = 2751505.0375 [kW] 
Hydrogen storage capacity = 8126065.55 [kg of H2] 
Battery energy capacity = 0.00 [kWh] 
Battery power capcity = 0.00 [kW]


### Post process data

In [13]:
path = r'C:\Nextcloud\HILT-CRC---Green-Hydrogen\DATA\SAM INPUTS\WEATHER_DATA'
weather_data = pd.read_csv(path + "\weather_data.csv",skiprows=2)


beam = weather_data['DNI'].tolist()
G_H = weather_data['GHI']
wind_speed = weather_data['Wind Speed']

water_rate = 15 #L/kgH2  range: 15-20 L/kgH2
c_wate = 5 # $/m3

#transfer the data from 'results' to a dataframe for plotting: 
data_plot = pd.DataFrame(dict(t = np.arange(0,len(simparams['L'])),
                              beam = beam,
                              G_H = G_H,
                              wind_speed = wind_speed,
                              pv_out=results['pv_out'], #kW
                              w_out=results['w_out'], #kW
                              pc=results['pc'], #kW
                              he_out = results['he_out'], #kg H2/s
                              hr_out = results['hr_out'], #kg H2/s
                              sh = results['sh'][0:-1], #kg H2
                              R = results['r'][0:-1], #kg H2/s 
                              L = results['L'], #kg H2/s
                              hs_out = (results['L']-results['hr_out']), #kg H2/s
                              bat_e_stored = results['bat_e_stored'][0:-1], #kWh
                              bat_pin = results['bat_pin'], #kW
                              bat_pout = results['bat_pout'], #kW
                              el_pin = results['el_pin'], #kW
                              water_mdot = results['he_out']*3.6*water_rate,  #T of H2O/hr
                              ))

#create a new column for datetime for plotting. This column is timestamped from the 
#beginning of 2022
data_plot['time'] =pd.to_datetime('2021-01-01') + pd.to_timedelta(data_plot.t, 'h')
data_plot.drop('t',axis=1,inplace=True)


## Plot solar irradiance and wind speed

In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.beam),
              line_shape='hv', name='Direct Solar Irrad. [W/m<sup>2</sup>]',
               line_color = 'red', opacity= 0.5, yaxis="y1"),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.G_H),
              line_shape='hv', name='Global H. Solar Irrad. [W/m<sup>2</sup>]',
               line_color = 'orange', opacity= 0.5, yaxis="y1"),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.wind_speed),
              line_shape='hv', name='Wind Speed [m/s]',
               line_color = 'green', opacity= 0.5, yaxis="y2"),
                )

fig.update_yaxes(dict(title = 'W/m<sup>2</sup>'),
                 linecolor='black',
                 mirror=True, secondary_y=False)

fig.update_yaxes(dict(title = 'm/s'), secondary_y=True)

fig.update_xaxes(linecolor='black',mirror=True)


fig.update_layout(width=900, height=300,
                  margin=dict(l=0, r=0, t=20, b=0))
path = r'C:\Users\Ahmad Mojiri\OneDrive - Australian National University\HILT CRC\Hydrogen supply HILTCRC\Pictures'
# fig.write_image(path + r'\PVW-CF=%s.png'%str(simparams['CF']))

fig.show()

### Plot mass flow

In [14]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
# fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.sh),
              name='H<sub>2</sub> Stored [T]',yaxis="y1"),
                )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.R),
#               name='R',yaxis="y1")
#                 )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.he_out),
              line_shape='hv',name='H<sub>2</sub> from Electrolyser [T/hr]',
               yaxis="y2", opacity=0.5)
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.hs_out),
              line_shape='hv',name='H<sub>2</sub> from Storage [T/hr]',yaxis="y2")
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.hr_out),
              line_shape='hv',name='Unserved Load [T/hr]',yaxis="y2")
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.water_mdot),
              line_shape='hv',name='Water to Electrolyser [T/hr]',
               opacity = 0.5, yaxis="y2")
                )

fig.update_yaxes(dict(title = '<b>kg of H<sub>2</sub></b>',linecolor='black',
                          mirror=True ), secondary_y=False,)

fig.update_yaxes(dict(title = '<b>kg/s</b>',linecolor='black',
                          mirror=True,), secondary_y=True)

fig.update_xaxes(dict(linecolor='black',
                          mirror=True))

fig.add_annotation(text='<b>Capacity Factor = %s</b>'%str(simparams['CF']),
                   xref="paper", yref="paper",
                   align='center',
                   x=0.5, y=0.95, showarrow=False)

fig.update_layout(width=900, height=300,
                  margin=dict(l=0, r=0, t=30, b=0))
path = r'C:\Users\Ahmad Mojiri\OneDrive - Australian National University\HILT CRC\Hydrogen supply HILTCRC\Pictures'
# fig.write_image(path + r'\Hflow-CF=%s.png'%str(simparams['CF']))
fig.show()

### Plot power flow

In [6]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
# Create figure
# fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.pv_out),
              line_shape='hv', name='PV Generation [kW]',
              line_color = 'orange', opacity= 0.5),
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.w_out),
              line_shape='hv', name='Wind Generation [kW]',
              line_color = 'green', opacity = 0.5),
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.pc),
              line_shape='hv', name='Curtailed Power [kW]',
              line_color = 'grey', opacity = 0.5),
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.bat_pin),
              line_shape='hv', name='Battery Charging [kW]'),
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.bat_pout),
              line_shape='hv', name='Battery Discharging [kW]'),
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.el_pin),
              line_shape='hv', name='Electrolyer Pin [kW]', yaxis="y1"),
                )
fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.bat_e_stored),
              line_shape='hv', name='Battery Energy [kWh]', yaxis="y2"),
                )


fig.update_yaxes(dict(title = 'kW',linecolor='black',
                          mirror=True ), secondary_y=False,)

fig.update_yaxes(dict(title = 'kWh',linecolor='black',
                          mirror=True,), secondary_y=True)

fig.update_xaxes(dict(linecolor='black',
                          mirror=True))

fig.add_annotation(text='<b>Capacity Factor = %s</b>'%str(simparams['CF']),
                   xref="paper", yref="paper",
                   align='center',
                   x=0.5, y=0.95, showarrow=False)

fig.update_layout(width=900, height=300,
                  margin=dict(l=0, r=0, t=20, b=0))
path = r'C:\Users\Ahmad Mojiri\OneDrive - Australian National University\HILT CRC\Hydrogen supply HILTCRC\Pictures'
# fig.write_image(path + r'\Pflow-CF=%s.png'%str(simparams['CF']))

fig.show()